In [20]:
import os
import re
import json

def load_translations(json_file):
    with open(json_file, 'r', encoding='utf-8') as f:
        return json.load(f)

def to_camel_case(s):
    parts = s.split('_')
    return parts[0].lower() + ''.join(word.capitalize() for word in parts[1:])


def replace_content(content, pattern, translations):
    matches = pattern.findall(content)
    for match in matches:
        translation_key = match.strip()
        translated_value = translations.get(translation_key, "")
        replacement = f'<ng-container i18n="@@{to_camel_case(translation_key)}">{translated_value}</ng-container>'
        content = re.sub(r"(?<!\"){{\s*'"+re.escape(translation_key)+r"'\s*\|\s*oldTranslate\s*}}", replacement, content)
    
def replace_attributes(content, attr_pattern, translations):
    matches = attr_pattern.findall(content)
    for match in matches:
        full_match, translation_key = match
        translation_key = translation_key.strip()
        camel_case_key = to_camel_case(translation_key)
        new_key = f"@@{camel_case_key}"
        translated_value = translations.get(translation_key, "")
        replacement = f'i18n-{full_match.split("=")[0].strip().strip("[]")}="{new_key}" {full_match.split("=")[0].strip().strip("[]")}="{translated_value}"'
        content = content.replace(full_match, replacement)
    return content


def search_in_html_files(folder_path, regex):
    # Compile the regex pattern
    pattern = re.compile(regex)
    attr_pattern = re.compile(attr_regex)
    attr_block_pattern = re.compile(attr_block_regex)
    
    # Iterate over all files in the folder
    for root, _, files in os.walk(folder_path):
        for file in files:
            if file.endswith(".html"):
                file_path = os.path.join(root, file)
                with open(file_path, 'r', encoding='utf-8') as f:
                    content = f.read()
                    content = replace_attributes(content, attr_block_pattern, translations)
                with open(file_path, 'w', encoding='utf-8') as f:
                    f.write(content)

# Usage
folder_path = 'C:/Users/rescl/IdeaProjects/unity-client-ts/src/app'
json_file = 'C:/Users/rescl/IdeaProjects/unity-client-ts/src/translations/unity-nl.json'
regex = r"(?<!\"){{\s*'([^']*)'\s*\|\s*oldTranslate\s*}}"
attr_regex = r"(\w+\s*=\"{{\s*\'([^']*)\'\s*\|\s*oldTranslate\s*}}\")"
attr_block_regex = r"(\[\w+\s*\]=\"\s*\'([^']*)\'\s*\|\s*oldTranslate\s*\")"

translations = load_translations(json_file)
search_in_html_files(folder_path, regex)